In [1]:
# Plotting and analysis
# behavior figures

# looking at bulk tuning curves in one plot for ACx and IC

#%% file import pre procesing
import pandas as pd
import numpy as np



#plots
import matplotlib.pyplot as plt
import seaborn as sns

from scipy.signal import savgol_filter

from array import *


print(pd.__version__)

from scipy.ndimage import median_filter

import auto_tuning_functions as auto_tune

2.2.1
2.2.1


In [2]:
# frequency and intensity list for later
freq_ls = [1000.,  1500.,  2000.,  3000.,  4000.,  6000.,  8000., 12000.,
    16000., 20000., 24000., 30000., 35000., 40000., 45000., 50000.,
    55000., 60000., 65000.]



db_ls = [0,10,20,30,40,50,60,70,80,90]

df1 = pd.read_pickle('acx_spks') # load in spiking data
df2 = pd.read_pickle('acx_spks_2')
ac_spks = pd.concat([df1,df2]) # append spiking data


evoked_df = auto_tune.make_evoked_df(ac_spks,freq_ls,db_ls)
db_df = auto_tune.make_dB_df(evoked_df=evoked_df)

                                                   0  \
0  [False, -0.01488928000004764, 36, 0.005, 26.78...   
1  [False, -0.039848320000012344, 32, 0.005, 23.1...   
2  [True, 0.010807039999926896, 30, 0.08, 24.0371...   
3  [True, 0.09039744000002876, 30, 0.0, 22.666666...   
4  [False, -0.039397760000192655, 34, 0.005, 25.2...   
5  [True, 0.025110719999838646, 33, 0.0, 24.97534...   
6  [False, 0.010151679999930788, 33, 0.005, 24.65...   
7  [False, -0.044602560000084855, 36, 0.005, 26.1...   
8  [True, 0.02006976000008759, 32, 0.0, 24.154265...   
9  [True, 0.02031551999995823, 60, 0.015, 51.8335...   

                                                   1  \
0  [True, 0.05502880000010914, 31, 0.03, 23.59129...   
1  [False, 0.0901926399997955, 33, 0.005, 24.4871...   
2  [True, 0.02015168000004447, 34, 0.01, 26.51998...   
3  [False, -0.044602560000084855, 21, 0.005, 15.6...   
4  [False, 0.08539743999991507, 28, 0.005, 20.666...   
5  [False, -0.019930239999969235, 28, 0.005, 19

/home/auerbach1/Desktop/fmr1_sd_fra_analysis/auto_tuning_functions.py:275: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  plot_df = plot_df._append({'latency': lat_mean, 'abs_peak_fr': peak_mean,


0     11
3     13
5     11
11    10
dtype: int64
3     10
5     10
8     10
11    14
13    11
16    12
dtype: int64
2     20
9     14
11    17
12    23
14    16
15    26
17    16
dtype: int64
2     20
3     14
7     13
8     15
11    16
12    14
14    40
dtype: int64
4     14
5     22
9     19
10    24
11    21
12    18
13    20
14    34
15    41
16    40
17    38
dtype: int64
2     15
4     18
6     16
7     20
8     14
10    22
11    19
13    25
14    41
15    42
16    33
17    42
18    33
dtype: int64
1     13
2     14
5     47
6     26
7     17
8     25
9     35
10    32
12    33
13    27
14    43
15    44
16    50
17    33
18    30
dtype: int64
0     14
2     34
3     31
4     63
5     46
6     59
7     38
8     39
10    45
11    38
12    34
13    32
14    45
16    45
17    42
18    30
dtype: int64
1     44
2     45
4     50
5     55
6     51
7     53
8     42
9     43
10    52
11    44
12    41
13    34
14    39
16    46
17    44
18    35
dtype: int64
                            

In [95]:
def get_thresh(current_dbx1_array,db_ls):

# Smooth the line
    
    smoothed_y = savgol_filter(current_dbx1_array, window_length=5, polyorder=3)


    #thresh = 0.2*np.max(y)
    maxi=np.max(smoothed_y)
    addi = 0.1*maxi
    thresh_y = np.min(smoothed_y)+addi
    #print(thresh_y)

    thresh_rounded = round(thresh_y, 0)# round to nearestwhole number both thresh and smoothed Y
    smooth_rounded = np.round(smoothed_y, 0)
    #print(thresh_rounded,smooth_rounded)


     
    int_ind = np.where(smooth_rounded == thresh_rounded) # if there is an equal value then we are good
        



    
    #print(int_ind)
    try:
        thresh_ind = int_ind[0][0] # need to get the corresponding x value intensity
        #print('Not Empty')
    except:
        # if no equal value need to find the closest one to get the intensity index
        thresh_diff_array = smooth_rounded-thresh_rounded # need to get the closest smoothed value to our threshold fr
        smallest_diff = np.min(abs(thresh_diff_array))
        thresh_ind = np.where(abs(thresh_diff_array) == smallest_diff)
        #print('It was empty: ',smallest_diff,thresh_diff_array,thresh_ind)
        #print(thresh_ind[0][0])
        thresh_ind = thresh_ind[0][0]

    
    thresh_db = db_ls[thresh_ind]
    #print(thresh_db)

    return thresh_db


def test_thresh_col(dB_df,db_ls):

    
    thresh_df = pd.DataFrame(columns = ['threshold','file','channel','genotype'])
    intensity = db_ls

    for i in dB_df['file'].unique(): # need ti group by file and by channel
        current_file = dB_df.loc[dB_df['file'] == i]
        for j in current_file['channel'].unique():
            #print(j)
            current_unit = current_file.loc[current_file['channel'] == j]
            #print(current_unit)
            current_geno = current_unit['genotype'] # grab the current genotype
            #print(current_geno)
            
            if isinstance(current_geno, str):
                current_geno = current_geno
            else:
                current_geno = 'WT' # weird error were some geno labels were saved in an array

            curr_fr = current_unit['rel_peak_fr'] 
     
            thresh = get_thresh(curr_fr,intensity)

                # make a threshold dataframe columns being threshold, file, channel, genotype
            thresh_df = thresh_df._append({'threshold': thresh,
                                                    'file': i,
                                                    'channel':j,
                                                    'genotype' : current_geno}, ignore_index=True)

            


    return thresh_df


In [97]:
smoothed = test_thresh_col(db_df,db_ls)
smoothed

Not Empty
20
It was empty:  1.0 [-6. -6. -4. -1.  3.  7. 10. 16. 21. 24.] (array([3]),)
30
Not Empty
30
It was empty:  1.0 [-2. -4. -2.  1.  2.  4. 10. 17. 24. 29.] (array([3]),)
30
Not Empty
30
It was empty:  1.0 [-3. -5. -1.  2.  7.  9. 12. 17. 24. 30.] (array([2]),)
20
It was empty:  1.0 [-4. -3. -2. -1.  1.  3.  6. 11. 17. 19.] (array([3, 4]),)
30
Not Empty
30
It was empty:  1.0 [-2. -3. -3.  1.  4.  6.  8. 12. 15. 16.] (array([3]),)
30
It was empty:  1.0 [-3. -2. -1.  1.  2.  3.  8. 12. 15. 16.] (array([2, 3]),)
20
Not Empty
30
Not Empty
30
Not Empty
30
Not Empty
30
Not Empty
20
It was empty:  1.0 [-6. -2. -1.  4. 10. 13. 16. 20. 26. 30.] (array([2]),)
20
It was empty:  1.0 [-6. -4. -3.  1.  7. 15. 22. 28. 34. 40.] (array([3]),)
30
Not Empty
30
It was empty:  2.0 [-4. -4. -2.  2.  8. 14. 19. 25. 29. 27.] (array([2, 3]),)
20
It was empty:  1.0 [-3. -3. -3. -1.  1.  4.  8. 14. 23. 29.] (array([3, 4]),)
30
Not Empty
30
It was empty:  1.0 [-1. -2. -1.  2.  6.  9. 12. 15. 16. 19.] (arr

threshold                                   file channel genotype
0          20  F:\Fmr1 SD Tanks\WT\BA190305A\Block-2       1       WT
1          30  F:\Fmr1 SD Tanks\WT\BA190305A\Block-2       2       WT
2          30  F:\Fmr1 SD Tanks\WT\BA190305A\Block-2       3       WT
3          30  F:\Fmr1 SD Tanks\WT\BA190305A\Block-2       4       WT
4          30  F:\Fmr1 SD Tanks\WT\BA190305A\Block-2       5       WT
..        ...                                    ...     ...      ...
443        20  F:\Fmr1 SD Tanks\KO\BA190328E\Block-3      12       WT
444        20  F:\Fmr1 SD Tanks\KO\BA190328E\Block-3      13       WT
445        10  F:\Fmr1 SD Tanks\KO\BA190328E\Block-3      14       WT
446        20  F:\Fmr1 SD Tanks\KO\BA190328E\Block-3      15       WT
447        20  F:\Fmr1 SD Tanks\KO\BA190328E\Block-3      16       WT

[448 rows x 4 columns]

In [3]:
#new_df.to_csv('ACx_wt_v_ko_peak_latency_duration_firstsd4bin.csv')# save dataframe as csv
#new_df = pd.read_csv('wt_v_ko_peak_latency_duration.csv')
#plot_df.to_csv('ACx_simple_wt_v_ko_peak_latency_duration_firstsd4bin.csv')# save dataframe as csv

#ACx_io_int = pd.read_csv('ACx_simple_wt_v_ko_peak_latency_duration_firstsd4bin.csv')
#ACx_io_spks = plot_df

#ACx_io_spks['intensity'] = ACx_io_int['intensity']
#ACx_io_spks.file.unique()


current_file = 'F:\\Fmr1 SD Tanks\\WT\\BA190305C\\Block-2'
chan = 6
currenf_df = ACx_io_spks.loc[ACx_io_spks['file'] == current_file]
currenf_df = currenf_df.loc[currenf_df['channel'] == chan]


wt_intensity = currenf_df.loc[currenf_df['genotype'] == 'WT']
wt_intensity = wt_intensity['intensity']


wt_fr = currenf_df.loc[currenf_df['genotype'] == 'WT']
wt_fr = wt_fr['rel_peak_fr']

In [ ]:
# plot
# plot WT vs KO 

sns.set_context("talk")
sns.set_style("white")

fig1,ax1 = plt.subplots(figsize=(5,5))
colors = ["#808080","#FF0B04" ]
sns.set_palette(sns.color_palette(colors))




#plt.figure(figsize=(12,5))
sns.lineplot(data=ACx_io_spks,x='intensity',y='smoothed_data',hue='genotype')
#plt.figlegend(loc='upper left')

plt.title('ACx Corrected Peak FR')
plt.ylabel('Spike (#)')
plt.xlabel('Genotype')

sns.despine()
plt.legend([],[], frameon=False)
plt.figlegend(loc='center')
plt.tight_layout()
#plt.savefig('last_bin_latency_ACx_violin.svg',dpi=600)

In [ ]:
# Example usage
# Generate example data



In [ ]:
plot_df
plot_df['latency'] = plot_df['latency']*1000
plot_df['resp_duration'] = plot_df['resp_duration']*1000
plot_df['first_bin'] = plot_df['first_bin']*1000
plot_df['last_bin'] = plot_df['last_bin']*1000


# plot WT vs KO 


sns.set_context("talk")
sns.set_style("white")

fig1,ax1 = plt.subplots(figsize=(5,5))
colors = ["#808080","#FF0B04" ]
sns.set_palette(sns.color_palette(colors))

#plt.figure(figsize=(12,5))
sns.violinplot(data=plot_df,x='genotype',y='last_bin',hue='genotype')
#plt.figlegend(loc='upper left')

plt.title('ACx Last Bin Latency')
plt.ylabel('Latency (ms)')
plt.xlabel('Genotype')

sns.despine()
plt.legend([],[], frameon=False)
plt.figlegend(loc='center')
plt.tight_layout()
plt.savefig('last_bin_latency_ACx_violin.svg',dpi=600)

In [ ]:
# plot WT vs KO 

sns.set_context("talk")
sns.set_style("white")

fig1,ax1 = plt.subplots(figsize=(5,5))
colors = ["#808080","#FF0B04" ]
sns.set_palette(sns.color_palette(colors))

#plt.figure(figsize=(12,5))
sns.violinplot(data=plot_df,x='genotype',y='last_bin',hue='genotype')
#plt.figlegend(loc='upper left')

plt.title('ACx Last Bin Latency')
plt.ylabel('Latency (ms)')
plt.xlabel('Genotype')

sns.despine()
plt.legend([],[], frameon=False)
plt.figlegend(loc='center')
plt.tight_layout()
#plt.savefig('last_bin_latency_ACx_violin.svg',dpi=600)